In [2]:
#imports
import z3

In [3]:
#load small input
input = open("./../../data/day_24/small_input.txt", "r").readlines()
min_val = 7
max_val = 27

In [8]:
#load small input
input = open("./../../data/day_24/input.txt", "r").readlines()
min_val = 200000000000000
max_val = 400000000000000

In [9]:


trajs = []
for line in input:
    line = line.strip().replace(" ","")
    pos,vel = line.split("@")
    pos,vel = [int(p) for p in pos.split(",")], [int(v) for v in vel.split(",")]
    trajs.append( (pos,vel) )

In [22]:
#probably, comparing each two and calculating their intersection is the fastest way, because the occupancy grid would be too large to store :(
#x1 + v1*t = x2 + v2*t
#x1-x2 = v2*t-v1*t
#x1-x2 = (v2-v1)*t
#(x1-x2)/(v2-v1) = t

"""
x1+vx1*t1 = x2+vx2*t2
y1+vy1*t1 = y2+vy2*t2
"""
crossing_paths = 0
for i,(pos1,vel1) in enumerate(trajs[:-1]):
    for j,(pos2,vel2) in enumerate(trajs[i+1:]):
        print(f"Check Traj {i} and {j+i+1}")
        #calculate t from the x coordinates
        if (vel2[0]-vel1[0]) == 0:
            if pos1[0] == pos2[0]:
                t = 0
            else:
                continue
        else:
            t = (pos1[0]-pos2[0])/(vel2[0]-vel1[0])
        if t < 0: 
            continue #the trajectories never cross in the future
        print(f"-> t = {t}")
        #calculate the x coordinate at time t
        x = pos1[0]+vel1[0]*t
        print(f"-> x = {x}")
        #calculate the y coordinates at time t
        y1 = pos1[1]+vel2[1]*t
        y2 = pos2[1]+vel2[1]*t
        print(f"-> y1 = {y1}, y2 = {y2}")
        if y1 != y2:
            continue
        else:
            #check for min and max
            if min_val <= x <= max_val and min_val <= y1 <= max_val:
                crossing_paths += 1

print(f"Part 1: There are {crossing_paths} crossing paths")

Check Traj 0 and 1
-> t = 641535473468.2368
-> x = 290417013677530.75
-> y1 = 159517331985045.75, y2 = 283767771191612.75
Check Traj 0 and 2
-> t = 629672014935.1523
-> x = 287724008590520.6
-> y1 = 221259871111608.25, y2 = 327919831615211.25
Check Traj 0 and 3
-> t = 803661200097.1205
-> x = 327219553622287.4
-> y1 = 82930750485670.12, y2 = 253520126365248.12
Check Traj 0 and 4
-> t = 774975422910.8402
-> x = 320707882201001.75
-> y1 = 164444301582833.38, y2 = 307356481706064.4
Check Traj 0 and 5
-> t = 543734740186.687
-> x = 268216247222618.94
-> y1 = 280265937968390.2, y2 = 283125317993683.2
Check Traj 0 and 6
-> t = 737717018316.211
-> x = 312250224358020.9
-> y1 = 908077958192726.9, y2 = 806587253840065.9
Check Traj 0 and 7
-> t = 506399978327.2586
-> x = 259741256280528.7
-> y1 = 138220120948286.78, y2 = 278402633414011.78
Check Traj 0 and 8
-> t = 837592627751.4622
-> x = 334921987699822.9
-> y1 = 295954433829442.44, y2 = 424955668030599.44
Check Traj 0 and 9
-> t = 51114662206

In [42]:
def almost_eq(a,b,eps=3):
    return abs(a-b) < eps

#probably, comparing each two and calculating their intersection is the fastest way, because the occupancy grid would be too large to store :(
# actual calculation with proper maths that uses different t1 and t2 instead of a single t
crossing_paths = 0
crossing_paths_b = 0
checked = 0
for i,(pos1,vel1) in enumerate(trajs[:-1]):
    for j,(pos2,vel2) in enumerate(trajs[i+1:]):
        checked += 1
        #print(f"Check Traj {i} and {j+i+1}")
        #calculate t1 
        al = vel2[0]/vel2[1]
        # if almost_eq( (vel1[0]-al*vel1[1]), 0):
        #     # print(f"-> div by 0, parallel")
        #     if pos1[0] == pos2[0]:
        #         t1 = 0
        #         t2 = 0
        #         print(f"Equal")
        #     else:
        #         print(f"div 0, al is {al}")
        #         continue
        # else:
        t1 = (al*pos1[1]-al*pos2[1]-pos1[0]+pos2[0])/(vel1[0]-al*vel1[1]+1e-20)
        t2 = (pos1[0]-pos2[0]+vel1[0]*t1)/vel2[0]

        if t1 < 0:
            # print(f"->Path1 in past")
            continue
        if t2 < 0:
            # print(f"->Path2 in past")
            continue

        x1,y1 = pos1[0]+vel1[0]*t1, pos1[1]+vel1[1]*t1
        x2,y2 = pos2[0]+vel2[0]*t2, pos2[1]+vel2[1]*t2
        if min_val <= x1 <= max_val and min_val <= y1 <= max_val:
                crossing_paths_b += 1
        if almost_eq(x1,x2) and almost_eq(y1,y2):
            if min_val <= x1 <= max_val and min_val <= y1 <= max_val:
                crossing_paths += 1
                # print(f"-> paths cross at {x1},{y1} at t1 = {t1} and t2 = {t2}")
            # else:
                # print(f"-> paths cross OUTSIDE at {x1},{y1} at t1 = {t1} and t2 = {t2}")
        # else:
        #     print(f"-> paths do NOT cross at {x1},{y1} / {x2},{y2} at t1 = {t1} and t2 = {t2}")
                

print(f"Part 1: There are {crossing_paths} / {crossing_paths_b} crossing paths out of {checked} checked pairs")
# -> sanity checked with reddit solution. Apparently, the difference due to floating point errors can be >= 1 for the positions, so the original solution always came out too low. Works with eps=3

Part 1: There are 16939 / 16939 crossing paths out of 44850 checked pairs


In [11]:
#solve part 2 using z3 solver
mx,my,mz,vmx,vmy,vmz = map(z3.Int, "mx my mz vmx vmy vmz".split())
solver = z3.Solver()
for i,(pos,vel) in enumerate(trajs):
    x,y,z = pos
    vx,vy,vz = vel
    t = z3.Int(f"t_{i}")
    solver.add(mx + vmx*t == x + vx*t)
    solver.add(my + vmy*t == y + vy*t)
    solver.add(mz + vmz*t == z + vz*t)

solver.check()
result = solver.model().eval(mx+my+mz)
print(f"Part 2: {result}")

Part 2: 931193307668256
